**NOTE**: Incomplete!!!

[Day 18](https://adventofcode.com/2019/day/18) puzzle input is a maze (mine is [here](puzzle_input/day18.txt)) where capital letters represent doors, that require keys (lower case letters) to open (i.e. you need to collect "a" if you want to traverse through door "A"). Part 1 involves finding the fastest route through this maze to collect all keys. Part 2 involves splitting the maze into quadrants and having four different things moving through the maze. Ugh.

I kind of hated this one too - it's like travelling salesman if after visiting a node the graph changed :-/

In [2]:
from itertools import combinations


def create_node_namer():
    n = 0
    while True:
        yield f"_{n}"
        n += 1
        
def is_space(s):
    return s == "."

def is_wall(s):
    return s == "#"

def is_connecting(s):
    return s[0] == "_"

def is_key(s):
    if (len(s) > 1):
        return False
    
    return ord(s) >= ord("a") and ord(s) <= ord("z")
    
def is_door(s):
    if (len(s) > 1):
        return False
    
    return ord(s) >= ord("A") and ord(s) <= ord("Z")

def graph_delete(graph, node, ignore_error=False):
    if not node in graph:
        if ignore_error:
            return
        raise Exception(f"Node {node} was not found in graph, can't delete")
    
    neighbours = graph[node]
    new_edges = list(combinations([n for n in neighbours], 2))
    
    for edge in new_edges:
        node_1, node_2 = edge
        new_distance = neighbours[node_1] + neighbours[node_2]
        
        # we can add this edge if:
        #   1. the nodes weren't already connected
        #   2. the nodes were connected, but this edge is cheaper
        if (not node_2 in graph[node_1]) or graph[node_1][node_2] > new_distance:
            graph[node_1][node_2] = new_distance
            graph[node_2][node_1] = new_distance

    # finally clean up all references to our old node
    for neighbour in neighbours:
        del graph[neighbour][node]
    del graph[node]
    
    
def cheapest_next_key(graph, from_node):
    neighbours = graph[from_node]
    neighbouring_keys = [ n for n in neighbours if is_key(n) ]
    sorted_neighbouring_keys = sorted(neighbouring_keys, key=lambda n: neighbours[n])
    return sorted_neighbouring_keys[0]

def shake_graph(graph):
    should_delete_door = lambda node: is_door(node) and len(graph[node]) == 1
    should_delete_connector = lambda node: is_connecting(node) and len(graph[node]) < 3
    nodes_to_delete = [ node for node in graph if should_delete_door(node) or should_delete_connector(node) ]
            
    while nodes_to_delete:
        for node in nodes_to_delete:
            graph_delete(graph, node)
        nodes_to_delete = [ node for node in graph if should_delete_door(node) or should_delete_connector(node) ]

def parse_maze(maze_str):
    # 1. split into lines, and then lines into list of strings: ("a...b" => [ "a", ".", ".", ".", "c"])
    maze_lines = []
    for line_str in maze_str.split("\n"):
        maze_lines.append([c for c in line_str])

    # 2. find the spaces that connect two levels vertically, and swap in a string with a name that
    #    doesn't clash like "_1"
    connecting_tiles = []
    for line_idx, line in enumerate(maze_lines):
        for tile_idx, tile in enumerate(line):
            # we don't want to replace if it's a wall or non-space
            if is_wall(tile) or not is_space(tile):
                continue
                
            should_replace = False
            if line_idx > 0:
                tile_above = maze_lines[line_idx - 1][tile_idx]
                if not is_wall(tile_above):
                    should_replace = True

            if line_idx < len(maze_lines):
                tile_below = maze_lines[line_idx + 1][tile_idx]
                if not is_wall(tile_below):
                    should_replace = True

            if should_replace:
                connecting_tiles.append((line_idx, tile_idx))

    namer = create_node_namer()
    for (line_idx, tile_idx) in connecting_tiles:
        maze_lines[line_idx][tile_idx] =  next(namer)


    # 3. start creating the graph by finding horizontal edges
    #    so for "a...b" we'll add {"a": {"b": 4}, "b": {"a": 4}}
    from collections import defaultdict
    graph = defaultdict(dict)
    for line_idx, line in enumerate(maze_lines):
        current_node = None
        current_count = 0
        for tile_idx, tile in enumerate(line):
            current_count += 1

            # if we hit a wall, we need to reset current_node/count
            if is_wall(tile):
                current_node = None
                current_count = 0
                continue

            if not is_space(tile):
                if current_node:
                    graph[current_node][tile] = current_count
                    graph[tile][current_node] = current_count
                current_node = tile
                current_count = 0

    # 4. add the vertical edges (they'll reach DOWN until they find a non-space node)
    for line_idx, line in enumerate(maze_lines):
        for tile_idx, tile in enumerate(line):
            if is_wall(tile) or is_space(tile):
                continue

            count = 0

            next_line_idx = line_idx + 1
            while next_line_idx < len(maze_lines):
                count += 1
                next_tile = maze_lines[next_line_idx][tile_idx]
                
                if is_space(next_tile):
                    next_line_idx += 1
                    continue
                    
                if is_wall(next_tile):
                    break
                
                graph[tile][next_tile] = count
                graph[next_tile][tile] = count
                break

    # 5. finally we'll make a pass to remove:
    #    - doors that have only one neighbour (dead end)
    #    - connectors unless they're a real choice (>2 neighbours)
    #    and update graph accordingly. we'll need to do this until we return no nodes to delete
    should_delete_door = lambda node: is_door(node) and len(graph[node]) == 1
#     should_delete_connector = lambda node: is_connecting(node) and len(graph[node]) < 3
    should_delete_connector = lambda node: is_connecting(node) 

    nodes_to_delete = [ node for node in graph if should_delete_door(node) or should_delete_connector(node) ]
            
    while nodes_to_delete:
        for node in nodes_to_delete:
            graph_delete(graph, node)
        nodes_to_delete = [ node for node in graph if should_delete_door(node) or should_delete_connector(node) ]
    
    return graph


In [1]:
from copy import deepcopy
import math

class SearchState:
    def __init__(self, graph, current, visited, route, steps=0):
        self.graph = graph
        self.current = current
        self.visited = visited
        self.route = route
        self.steps = steps

    def move(self, node):
        neighbours = self.graph[self.current]
        
        if not (node in neighbours):
            raise Exception(f"cannot move from {self.current} to {node}. valid moves: {neighbours.keys}")
                
        visited = self.visited.union(set([node]))
        route = self.route + [node]
        steps = self.steps + neighbours[node]
        
        new_graph = deepcopy(self.graph)
        graph_delete(new_graph, self.current)
        if is_key(node):
            # ignore_error=True, in case there's no door for the key
            graph_delete(new_graph, node.upper(), True)
        
#         if all_keys.issubset(visited):
#             solutions.append(steps)
#             return None
        
        should_delete_door = lambda node: is_door(node) and len(new_graph[node]) == 1
        should_delete_connector = lambda node: is_connecting(node) and len(new_graph[node]) < 3
        nodes_to_delete = [ node for node in new_graph if should_delete_door(node) or should_delete_connector(node) ]

        while nodes_to_delete:
            for node in nodes_to_delete:
                graph_delete(new_graph, node)
            nodes_to_delete = [ node for node in new_graph if should_delete_door(node) or should_delete_connector(node) ]
        
        
        return SearchState(new_graph, node, visited, route, steps)
    
    def __repr__(self):
        return "->".join(self.route)    
    
    def __str__(self):
        return "->".join(self.route)
                            
def step(state):
    to_visit = [ node for node in state.graph[state.current] if not is_door(node) ]
    new_states = [ state.move(node) for node in to_visit ]
    return [ s for s in new_states if s ]

def step_all(states):
    new_states = []
    for state in states:
        new_states += step(state)
    # assume that anything outside the quickest 2048 so far are probably not the fastest solutions
    return sorted(new_states, key=lambda state: state.steps)[:10000]

def solve2(graph):
    global solutions
    global all_keys
    
    solutions = []
    all_keys = set([ node for node in graph if is_key(node) ])
    
    states = [
        SearchState(graph, "@", set(), [])
    ]
    
    while len(solutions) < 1:
        pprint(states)
        states = step_all(states)
        
    print(sorted(solutions)[0])
    print("----------------------------")

    
def solve_inner(state, indent=""):
    global all_keys
    global total
    global best

    # if we're already more than the limit, give up
    if best < state.steps:
        return math.inf
    
#     print(f"{indent}{state.current}")
    if all_keys.issubset(state.visited):
        total += 1
        
        if state.steps < best:
            best = state.steps
            print(f"new best: {best}")

        if total % 100 == 0:
            print(f"found {total} solutions")
        
        # print(f"new solution: {state.steps} (best is {best})")
        return state.steps

    neighbours = [ n for n in state.graph[state.current] if not is_door(n) ]
    
    if not neighbours:
        return math.inf
    
    return min([ solve_inner(state.move(n), indent+" ") for n in neighbours])


best = math.inf
total = 0
def solve(graph):
    global all_keys
    global best
    global total
    pprint(graph)
    
    total = 0
    all_keys = set([ node for node in graph if is_key(node) ])    
    best = math.inf
    ans = solve_inner(SearchState(graph, "@", set(), []))
    print(ans)
    print("------------------------")
    return ans

In [3]:

from pprint import pprint

solutions = []
all_keys = None

maze_str_0 = """#########
#b.A.@.a#
#########"""
graph_0 = parse_maze(maze_str_0)


maze_str_1 = """########################
#f.D.E.e.C.b.A.@.a.B.c.#
######################.#
#d.....................#
########################"""
graph_1 = parse_maze(maze_str_1)

maze_str_2 = """########################
#...............b.C.D.f#
#.######################
#.....@.a.B.c.d.A.e.F.g#
########################"""
graph_2 = parse_maze(maze_str_2)

maze_str_3 = """#################
#i.G..c...e..H.p#
########.########
#j.A..b...f..D.o#
########@########
#k.E..a...g..B.n#
########.########
#l.F..d...h..C.m#
#################"""
graph_3 = parse_maze(maze_str_3)

maze_str_4 = """########################
#@..............ac.GI.b#
###d#e#f################
###A#B#C################
###g#h#i################
########################"""
graph_4 = parse_maze(maze_str_4)


solve(graph_0)
solve(graph_1)
solve(graph_2)
solve(graph_3)
solve(graph_4)

defaultdict(<class 'dict'>,
            {'@': {'A': 2, 'a': 2},
             'A': {'@': 2, 'b': 2},
             'a': {'@': 2},
             'b': {'A': 2}})
new best: 8
8
------------------------
defaultdict(<class 'dict'>,
            {'@': {'A': 2, 'a': 2},
             'A': {'@': 2, 'b': 2},
             'B': {'a': 2, 'c': 2},
             'C': {'b': 2, 'e': 2},
             'D': {'E': 2, 'f': 2},
             'E': {'D': 2, 'e': 2},
             'a': {'@': 2, 'B': 2},
             'b': {'A': 2, 'C': 2},
             'c': {'B': 2, 'd': 24},
             'd': {'c': 24},
             'e': {'C': 2, 'E': 2},
             'f': {'D': 2}})
new best: 86
86
------------------------
defaultdict(<class 'dict'>,
            {'@': {'a': 2, 'b': 22},
             'A': {'d': 2, 'e': 2},
             'B': {'a': 2, 'c': 2},
             'C': {'D': 2, 'b': 2},
             'D': {'C': 2, 'f': 2},
             'F': {'e': 2, 'g': 2},
             'a': {'@': 2, 'B': 2},
             'b': {'@': 22, 'C': 2}

KeyboardInterrupt: 

In [4]:
puzzle_input_str = open("puzzle_input/day18.txt", "r").read()
puzzle_input = parse_maze(puzzle_input_str)

# doors = [ n for n in puzzle_input if is_door(n) ]

# door_neighbours = [ (d,len(puzzle_input[d])) for d in doors ]
# print(doors)
# print(len(puzzle_input.keys()))
# pprint(puzzle_input)
solve(puzzle_input)

defaultdict(<class 'dict'>,
            {'@': {'B': 131,
                   'E': 63,
                   'S': 27,
                   'T': 259,
                   'W': 239,
                   'Y': 275,
                   'e': 52,
                   'n': 194,
                   'o': 68,
                   's': 14,
                   'u': 32},
             'A': {'J': 26, 'a': 11, 'j': 7},
             'B': {'@': 131,
                   'E': 192,
                   'S': 156,
                   'T': 130,
                   'W': 370,
                   'Y': 146,
                   'e': 83,
                   'n': 65,
                   'o': 197,
                   's': 145,
                   'u': 161},
             'C': {'G': 90, 'K': 48, 'R': 72, 'Y': 26, 'a': 95, 'z': 3},
             'E': {'@': 63,
                   'B': 192,
                   'O': 18,
                   'S': 86,
                   'T': 320,
                   'W': 300,
                   'X': 34,
                   'Y'

KeyboardInterrupt: 

My algorithm is extremely suboptimal so I just kept this running for 10 minutes or so before coming back and trying the latest "new best" value (which was `3048`). This clearly won't work for Part 2 but I cannot motivate myself to revisit this and rewrite it from scratch.